## Get info of each game
Here are some examples of responded API:
- https://api.rawg.io/api/games/rimworld
- https://api.rawg.io/api/games/grand-theft-auto-v
- https://rawg.io/games/grand-theft-auto-v

In [1]:
import csv
import requests
import json
from pprint import pprint
from time import time
import concurrent.futures
import functools
import os

with open("../secret.json", "r") as f:
    API_KEY = json.load(f)["API_KEY"]
print(API_KEY)

030d55818d914e08a855fc51ee1b30cd


### Load CSV file which has game's id and its name

In [2]:
csv_data = []
with open("../data/game_id.csv", "r") as f:
    csv_data = list(csv.reader(f))

# Preview
for i, val in enumerate(csv_data):
    print(val)
    if i==10: break

['923617', 'nocturnal-forging']
['923616', 'vampirevania']
['923614', 'the-best-text-adventure-you-ever-done-did-play']
['923613', 'zombie-mayhem-zilox']
['923612', 'psychosis-5-ways']
['923611', 'the-mystery-of-bane-tavern-full-version']
['923610', 'trap-rooms-king-quest']
['923609', 'lost_wallet']
['923607', 'parkour-monek']
['923606', 'dort']
['923605', 'highlander-robot']


## Multithreading

### This function is responsible for requesting each game and save as a JSON file in `/data/game_info/`

In [3]:
def worker(start_index, games_per_worker, urls, downloaded_files, headers):
    for url in urls[start_index : start_index + games_per_worker]:
        if url.rsplit("/")[-1].split("?")[0] in downloaded_files: continue
        try:
            # Request API
            json_data = json.loads(requests.get(url, headers=headers).text)

            # Only include wanted keys
            D = {k:v for k,v in json_data.items() if k in include}

            # Clean up dictionary
            D["platforms"] = []
            for platform in json_data["platforms"]:
                D["platforms"].append(platform["platform"]["name"])

            for key in ("developers", "genres", "publishers"):
                D[key] = []
                for data in json_data[key]:
                    D[key].append(data["name"])

            if json_data["esrb_rating"]:
                D["esrb_rating"] = json_data["esrb_rating"]["name"]
            
            # Save as JSON file
            name = D["id"]
            with open(f"../data/game_info/{name}.json","w", encoding="utf-8") as f:
                json.dump(D, f)
        except:
            print(f"Error with {url}")

In [4]:
# Create folder if not existed
if not os.path.exists('../data/game_info/'):
    os.makedirs('../data/game_info/')

#### Threading Preparation

In [5]:
# column: name, developer, publisher, released, playtime, achievement_count, esrb, description, image 
headers = { 'User-Agent': 'App Name: Education purpose',}
params = {"key": API_KEY}
include = {"id",
           "slug",
           "name",
           "name_original",
           "metacritic",
           "released",
           "tba",
           "updated",
           "website",
           "rating",
           "rating_top",
           "added_by_status",
           "playtime",
           "achievements_count",
           "ratings_count",
           "suggestions_count",
           "game_series_count",
           "reviews_count",
           "platforms",
           "developers",
           "genres",
           "publishers",
           "esrb_rating",
           "description",
           "background_image"
           }

# Set up number of workers
max_workers = 64
start_game_index = 0
end_game_index = len(csv_data)
number_of_games = end_game_index - start_game_index
games_per_worker = int(number_of_games/max_workers) + 1 
start_index = range(start_game_index, end_game_index, games_per_worker)

# Make urls
base_url = "https://api.rawg.io/api/games/"
urls = [base_url + csv_data[i][0] + "?key="+API_KEY for i in range(len(csv_data))]

In [7]:
# Skip downloaded files
downloaded_files = {file.split(".",1)[0] for file in os.listdir("../data/game_info/")}

# Time
t0 = time()
with concurrent.futures.ThreadPoolExecutor(max_workers=max_workers) as executor:
    temp = functools.partial(worker,
                             games_per_worker=games_per_worker,
                             urls=urls,
                             downloaded_files=downloaded_files,
                             headers=headers,
                            )
    executor.map(temp, start_index)
    
# Time
print(f"Time taken: {time()-t0}")

Error with https://api.rawg.io/api/games/551998?key=030d55818d914e08a855fc51ee1b30cdError with https://api.rawg.io/api/games/353800?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/416098?key=030d55818d914e08a855fc51ee1b30cd

Error with https://api.rawg.io/api/games/39690?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/135393?key=030d55818d914e08a855fc51ee1b30cdError with https://api.rawg.io/api/games/191874?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/886841?key=030d55818d914e08a855fc51ee1b30cd

Error with https://api.rawg.io/api/games/613843?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/65480?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/935835?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/37195?key=030d55818d914e08a855fc51ee1b30cdError with https://api.rawg.io/api/games/20949?key=030d55818d914e08a8

KeyboardInterrupt: 

Error with https://api.rawg.io/api/games/897003?key=030d55818d914e08a855fc51ee1b30cdError with https://api.rawg.io/api/games/111700?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/241238?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/897034?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/476998?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/183927?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/732365?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/321971?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/553506?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/732357?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/850707?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/274217?key=030d55818d914e

Error with https://api.rawg.io/api/games/972184?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/131179?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/476989?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/503845?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/321959?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/787998?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/409464?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/262493?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/274212?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/69947?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/838443?key=030d55818d914e08a855fc51ee1b30cd
Error with https://api.rawg.io/api/games/35642?key=030d55818d914e0